In [1]:
import glob, os
import pathlib
import json
import yaml

import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import collections
from pprint import pprint
import re

from dotty_dict import dotty

%matplotlib inline

In [2]:
# avoid the module's method call deprecation
try:
    collectionsAbc = collections.abc
except AttributeError:
    collectionsAbc = collections

Configuring Juputer's options to present more things to the output.

In [3]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)

# Load Data GroundTruth

## Path declaration

In [4]:
path_config = os.path.join(os.getcwd(), "project_danceability.yaml")

In [5]:
path_app = os.path.join(os.path.abspath(os.getcwd()), os.pardir)
# path = os.path.join(path, 'danceability', 'features', 'mp3')
print('Current path:', path_app)
print('Type:', type(path_app))

Current path: /home/iotlab_user/Desktop/google2020/gsoc_ml_infrastructure/notebooks/..
Type: <class 'str'>


## Count all the JSON data included in files

In [6]:
counter = 0
for root, dirs, files in os.walk(path_app):
    for file in files:
        if file.endswith(".json"):
#             print(os.path.join(root, file))
            counter += 1
            
print('counted json files:', counter)

counted json files: 10461


## Load the GroundTruth file

In [7]:
with open(os.path.join(path_app, 'acousticbrainz-datasets/danceability/metadata/groundtruth.yaml'), 'r') as stream:
    try:
        groundTr_data = yaml.safe_load(stream)
    except yaml.YAMLError as exc:
        print(exc)

In [8]:
len(groundTr_data['groundTruth'].keys())

225

## Check the unique folders with tracks and sort them alphabetically

In [9]:
labeled_tracks = groundTr_data['groundTruth']

### Split the keys in Folder - Track Name

In [10]:
folders = []
for key in labeled_tracks:
    key = key.split('/')
    folders.append(key[0])

In [11]:
print(folders[:15])

['Alternative', 'Alternative', 'Alternative', 'Alternative', 'Alternative', 'Alternative', 'Alternative', 'Alternative', 'Alternative', 'Blues', 'Blues', 'Blues', 'Blues', 'Blues', 'Blues']


### Check the folders

In [12]:
folders = set(folders)
folders = list(folders)
folders.sort()
folders

['Alternative',
 'Blues',
 'Classical',
 'Country',
 'Dance and House',
 'Folk and New Age',
 'Hip-Hop and Rap',
 'House & Garage and Grime',
 'Jazz',
 'Jungle and D&B',
 'Latin',
 'Pop',
 'R&B and Soul',
 'Reggae',
 'Rock and Metal',
 'Techno and Electro',
 'Vocal and Acapella']

## Class Name retrieved from GT file

In [13]:
class_name = groundTr_data['className']

In [14]:
class_name

'danceability'

# Load a DF containing all the tracks (features + GT data)

In [15]:
path_features = os.path.join(path_app, 'acousticbrainz-datasets', 'danceability', 'features')
low_level_dir = ''
if len(os.listdir(path_features)) == 0:
    print("Directory is empty")
else:
    print("Directory is not empty")
    directory_contents = os.listdir(path_features)
    if 'mp3' in directory_contents:
        low_level_dir = 'mp3'
    elif 'orig' in directory_contents:
        low_level_dir = 'orig'
    else:
        low_level_dir = ''
        print('There is no valid low-level data inside the features directory')
print('Low-level directory:', low_level_dir)

Directory is not empty
Low-level directory: mp3


In [16]:
path_low_level = os.path.join(path_app, 'acousticbrainz-datasets/danceability', 'features', low_level_dir)

In [17]:
# path_low_level

In [18]:
if low_level_dir != '':
    tracks = []
    for key, value in labeled_tracks.items():
        track_dict = {}
        key = key.split('/')
        path_tracks = os.path.join(path_low_level, key[0])
        for f_name in os.listdir(path_tracks):
            if f_name.startswith(key[1]):
                track_dict['json_directory'] = key[0]
                track_dict['track'] = key[1]
                track_dict['track_path'] = os.path.join(path_low_level, key[0], f_name)
                track_dict['danceability'] = value
        tracks.append(track_dict)

In [19]:
len(tracks)

225

In [20]:
df_tracks = pd.DataFrame(data=tracks)

Plot the track's paths

In [21]:
df_tracks.head()

json_directory                                          track  \
0    Alternative         02 Happy Birthday - Altered Images.mp3   
1    Alternative                03 How Soon Is Now - Smiths.mp3   
2    Alternative  04 Pearly Dewdrops' Drops - Cocteau Twins.mp3   
3    Alternative                 06 Mr Brightside - Killers.mp3   
4    Alternative                           06 Song 2 - Blur.mp3   

                                                                                                                                                                                  track_path  \
0         /home/iotlab_user/Desktop/google2020/gsoc_ml_infrastructure/notebooks/../acousticbrainz-datasets/danceability/features/mp3/Alternative/02 Happy Birthday - Altered Images.mp3.json   
1                /home/iotlab_user/Desktop/google2020/gsoc_ml_infrastructure/notebooks/../acousticbrainz-datasets/danceability/features/mp3/Alternative/03 How Soon Is Now - Smiths.mp3.json   
2  /home/iotlab_user/Desktop/google2020/gsoc_ml_infrastructure/notebooks/../acousticbrainz-datasets/danceability/features/mp3/Alternative/04 Pearly Dewdrops' Drops - Cocteau Twins.mp3.json   
3                 /home/iotlab_user/Desktop/google2020/gsoc_ml_infrastructure/notebooks/../acousticbrainz-datasets/danceability/features/mp3/Alternative/06 Mr Brightside - Killers.mp3.json   
4                           /home/iotlab_user/Desktop/google2020/gsoc_ml_infrastructure/notebooks/../acousticbrainz-datasets/danceability/features/mp3/Alternative/06 Song 2 - Blur.mp3.json   

    danceability  
0      danceable  
1  not_danceable  
2  not_danceable  
3      danceable  
4      danceable

Check the className distribution of the data based on the 'genre_category'

Data distribution based on the genres

In [22]:
df_tracks['json_directory'].value_counts()

Latin                       22
Jungle and D&B              22
Dance and House             21
Hip-Hop and Rap             19
Vocal and Acapella          17
Techno and Electro          16
Folk and New Age            16
R&B and Soul                13
Rock and Metal              13
Reggae                      12
House & Garage and Grime    10
Alternative                  9
Blues                        8
Country                      8
Pop                          7
Classical                    6
Jazz                         6
Name: json_directory, dtype: int64

# Features DF

## Clean the low-level from the unnecessary features and load the rest to a list

Each index/item of the list contains the cleaned dictionary low-level data, flattened by the relevant function

In [23]:
def flatten_dict_full(d, sep="_"):
    obj = collections.OrderedDict()

    def recurse(t, parent_key=""):
        
        if isinstance(t, list):
            for i in range(len(t)):
                recurse(t[i], parent_key + sep + str(i) if parent_key else str(i))
        elif isinstance(t,dict):
            for k, v in t.items():
                recurse(v, parent_key + sep + k if parent_key else k)
        else:
            obj[parent_key] = t
    recurse(d)

    return obj

In [24]:
list_feats_tracks = []

In [25]:
list_feats_tracks.clear()  # clear the list if it not empty

counter_items_transformed = 0
for index, row in df_tracks.iterrows():
    f = open(row['track_path'])
    data_feats_item = json.load(f)

    # remove unnecessary data
    if 'beats_position' in data_feats_item['rhythm']:
      del data_feats_item['rhythm']['beats_position']
    
    # data dictionary transformed to a fully flattened dictionary
    data_feats_item = flatten_dict_full(data_feats_item)

    # append to a full tracks features pandas df
    list_feats_tracks.append(dict(data_feats_item))
    
    counter_items_transformed += 1

print('Items parsed and transformed:', counter_items_transformed)

Items parsed and transformed: 225


In [26]:
len(list_feats_tracks)

225

In [27]:
# list_feats_tracks

## Check a flattened low-level instance and save a sample locally

In [28]:
type(list_feats_tracks[0])

dict

In [29]:
example_dict = list_feats_tracks[0]

In [30]:
df_sample = pd.DataFrame.from_dict(example_dict, orient='index', columns=['low_level_data'])

In [31]:
df_sample.reset_index(level=0, inplace=True)

In [32]:
df_sample.columns = ['low_level_data', 'low_level_values']
df_sample.head()

low_level_data low_level_values
0        lowlevel_average_loudness         0.940232
1   lowlevel_barkbands_crest_dmean          2.76666
2  lowlevel_barkbands_crest_dmean2           4.4483
3    lowlevel_barkbands_crest_dvar          5.74581
4   lowlevel_barkbands_crest_dvar2          14.9876

In [33]:
df_sample.to_csv('sample_flattened_low_level_data.csv')

## Transform the low-level features instances to DF

In [34]:
df_feats_tracks = pd.DataFrame(list_feats_tracks, columns=list_feats_tracks[0].keys())

In [35]:
df_feats_tracks.head()

lowlevel_average_loudness  lowlevel_barkbands_crest_dmean  \
0                   0.940232                        2.766660   
1                   0.918468                        2.675291   
2                   0.903639                        2.680212   
3                   0.964146                        2.334805   
4                   0.923212                        2.654776   

   lowlevel_barkbands_crest_dmean2  lowlevel_barkbands_crest_dvar  \
0                         4.448297                       5.745806   
1                         4.377324                       6.211648   
2                         4.377909                       5.717108   
3                         3.876004                       6.314280   
4                         4.302909                       6.634628   

   lowlevel_barkbands_crest_dvar2  lowlevel_barkbands_crest_max  \
0                       14.987641                     26.722847   
1                       15.621523                     26.676046   
2                       13.717224                     24.490746   
3                       16.660341                     24.082594   
4                       16.935333                     26.224245   

   lowlevel_barkbands_crest_mean  lowlevel_barkbands_crest_median  \
0                      10.807129                         9.691339   
1                       8.789837                         8.108212   
2                       8.958855                         8.116771   
3                       7.989666                         7.193906   
4                       9.249996                         8.158960   

   lowlevel_barkbands_crest_min  lowlevel_barkbands_crest_var  \
0                      2.798266                     24.122204   
1                      2.419000                     12.385103   
2                      2.538304                     14.455623   
3                      2.510511                     11.031219   
4                      2.489789                     18.725180   

   lowlevel_barkbands_flatness_db_dmean  \
0                              0.023720   
1                              0.021670   
2                              0.020029   
3                              0.017094   
4                              0.020814   

   lowlevel_barkbands_flatness_db_dmean2  lowlevel_barkbands_flatness_db_dvar  \
0                               0.035958                             0.000526   
1                               0.033876                             0.000391   
2                               0.032708                             0.000378   
3                               0.027388                             0.000365   
4                               0.032149                             0.000563   

   lowlevel_barkbands_flatness_db_dvar2  lowlevel_barkbands_flatness_db_max  \
0                              0.001158                            0.627938   
1                              0.000961                            0.448718   
2                              0.000948                            0.291119   
3                              0.000918                            0.561661   
4                              0.001232                            0.386401   

   lowlevel_barkbands_flatness_db_mean  lowlevel_barkbands_flatness_db_median  \
0                             0.176747                               0.146083   
1                             0.113029                               0.105044   
2                             0.126804                               0.123771   
3                             0.096527                               0.074531   
4                             0.115602                               0.095726   

   lowlevel_barkbands_flatness_db_min  lowlevel_barkbands_flatness_db_var  \
0                            0.040839                            0.010974   
1                            0.025457                            0.001940   
2                            0.045240                  

In [36]:
df_feats_tracks.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 225 entries, 0 to 224
Columns: 2674 entries, lowlevel_average_loudness to tonal_key_scale
dtypes: float64(2575), int64(79), object(20)
memory usage: 4.6+ MB


In [37]:
df_feats_tracks.shape

(225, 2674)

## Concatenate the tracks DF with the feats DF

In [38]:
df_tracks.columns

Index(['json_directory', 'track', 'track_path', 'danceability'], dtype='object')

In [39]:
df_tracks.drop(labels=['track_path','json_directory',  'track'], axis=1, inplace=True)

In [40]:
df_full_tracks = pd.concat([df_tracks, df_feats_tracks], axis=1)

In [41]:
df_full_tracks.head()

danceability  lowlevel_average_loudness  lowlevel_barkbands_crest_dmean  \
0      danceable                   0.940232                        2.766660   
1  not_danceable                   0.918468                        2.675291   
2  not_danceable                   0.903639                        2.680212   
3      danceable                   0.964146                        2.334805   
4      danceable                   0.923212                        2.654776   

   lowlevel_barkbands_crest_dmean2  lowlevel_barkbands_crest_dvar  \
0                         4.448297                       5.745806   
1                         4.377324                       6.211648   
2                         4.377909                       5.717108   
3                         3.876004                       6.314280   
4                         4.302909                       6.634628   

   lowlevel_barkbands_crest_dvar2  lowlevel_barkbands_crest_max  \
0                       14.987641                     26.722847   
1                       15.621523                     26.676046   
2                       13.717224                     24.490746   
3                       16.660341                     24.082594   
4                       16.935333                     26.224245   

   lowlevel_barkbands_crest_mean  lowlevel_barkbands_crest_median  \
0                      10.807129                         9.691339   
1                       8.789837                         8.108212   
2                       8.958855                         8.116771   
3                       7.989666                         7.193906   
4                       9.249996                         8.158960   

   lowlevel_barkbands_crest_min  lowlevel_barkbands_crest_var  \
0                      2.798266                     24.122204   
1                      2.419000                     12.385103   
2                      2.538304                     14.455623   
3                      2.510511                     11.031219   
4                      2.489789                     18.725180   

   lowlevel_barkbands_flatness_db_dmean  \
0                              0.023720   
1                              0.021670   
2                              0.020029   
3                              0.017094   
4                              0.020814   

   lowlevel_barkbands_flatness_db_dmean2  lowlevel_barkbands_flatness_db_dvar  \
0                               0.035958                             0.000526   
1                               0.033876                             0.000391   
2                               0.032708                             0.000378   
3                               0.027388                             0.000365   
4                               0.032149                             0.000563   

   lowlevel_barkbands_flatness_db_dvar2  lowlevel_barkbands_flatness_db_max  \
0                              0.001158                            0.627938   
1                              0.000961                            0.448718   
2                              0.000948                            0.291119   
3                              0.000918                            0.561661   
4                              0.001232                            0.386401   

   lowlevel_barkbands_flatness_db_mean  lowlevel_barkbands_flatness_db_median  \
0                             0.176747                               0.146083   
1                             0.113029                               0.105044   
2                             0.126804                               0.123771   
3                             0.096527                               0.074531   
4                             0.115602                               0.095726   

   lowlevel_barkbands_flatness_db_min  lowlevel_barkbands_flatness_db_var  \
0                            0.040839                            0.010974   
1                            0.025457      

## Load config

In [42]:
with open(path_config, 'r') as conf_stream:
    try:
        config_data = yaml.safe_load(conf_stream)
    except yaml.YAMLError as exc:
        print(exc)

In [43]:
config_data

{'templateVersion': '2.1-beta2',
 'className': 'test_danceability',
 'datasetsDirectory': '/data/train_results_danceability/datasets',
 'resultsDirectory': '/data/train_results_danceability/results',
 'filelist': '/data/datasets/danceability/metadata/filelist_sig.yaml',
 'groundtruth': '/data/datasets/danceability/metadata/modified_groundtruth.yaml',
 'seed': 1593182276.72,
 'clusterMode': True,
 'excludedDescriptors': ['metadata.tags*'],
 'failOnUnmatched': False,
 'preprocessing': {'raw': [],
  'basic': [{'transfo': 'remove',
    'params': {'descriptorNames': ['metadata.*',
      '*dmean*',
      '*dvar*',
      '*.min',
      '*.max',
      '*cov',
      'tonal.thpcp',
      'lowlevel.spectral_energyband_high.*',
      'lowlevel.silence_rate*']}},
   {'transfo': 'enumerate',
    'params': {'descriptorNames': ['tonal.chords_key',
      'tonal.chords_scale',
      'tonal.key_key',
      'tonal.key_scale']}}],
  'lowlevel': [{'transfo': 'remove',
    'params': {'descriptorNames': ['met

In [44]:
config_data = dotty(config_data)

In [45]:
path_key_exclude_descr = config_data["excludedDescriptors"]
path_key_exclude_descr

['metadata.tags*']

In [46]:
path_preprocessing_selection = config_data["classifiers.svm"][0]["preprocessing"]
path_preprocessing_selection

['basic', 'lowlevel', 'nobands', 'normalized', 'gaussianized', 'mfcc']

In [47]:
path_preprocessing = config_data["preprocessing.{}".format(path_preprocessing_selection[0])]
path_preprocessing

[{'transfo': 'remove',
  'params': {'descriptorNames': ['metadata.*',
    '*dmean*',
    '*dvar*',
    '*.min',
    '*.max',
    '*cov',
    'tonal.thpcp',
    'lowlevel.spectral_energyband_high.*',
    'lowlevel.silence_rate*']}},
 {'transfo': 'enumerate',
  'params': {'descriptorNames': ['tonal.chords_key',
    'tonal.chords_scale',
    'tonal.key_key',
    'tonal.key_scale']}}]

In [48]:
# def make_lists_descr_handling(path_preprocessing):
#     transformations_dict = {}
#     counter = 0
#     for processing in path_preprocessing:
#         list_remove = []
#         list_enumerate = []
#         list_select = []
#         if processing["transfo"] == "remove":
#             print("descriptors to remove: {}".format(processing["params"]["descriptorNames"]))
#             list_remove = processing["params"]["descriptorNames"]
#             transformations_dict.update({processing["transfo"] + "{}".format(counter) : list_remove})
#             print()
#         elif processing["transfo"] == "enumerate":
#             print("descriptors to enumerate: {}".format(processing["params"]["descriptorNames"]))
#             list_enumerate = processing["params"]["descriptorNames"]
#             transformations_dict.update({processing["transfo"] + "{}".format(counter) : list_enumerate})
#             print()
#         elif processing["transfo"] == "select":
#             print("descriptors to select: {}".format(processing["params"]["descriptorNames"]))
#             list_select = processing["params"]["descriptorNames"]
#             transformations_dict.update({processing["transfo"] + "{}".format(counter) : list_select})
#             print()
#     return transformations_dict

In [49]:
# dict_transfo = make_lists_descr_handling(path_preprocessing)
# dict_transfo

In [50]:
len(df_full_tracks.columns)

2675

In [51]:
def list_descr_handler(descr_list):
    keys_list_handle = []
    for item in descr_list:
        if item.endswith(".*"):
            item = item.replace(".*", "_")
        elif item.startswith("*."):
            item = item.replace("*.", "_")
        else:
            item = item.replace("*", "")
        item = item.replace(".", "_")
        keys_list_handle.append(item)
    return keys_list_handle

In [52]:
def descr_selector(df, descr_select_list):
    columns_list = list(df.columns)
    columns_sel_list = []
    for item in descr_sel_list:
        for sel_item in columns_list:
            if re.search(item, sel_item):
                columns_sel_list.append(sel_item)
    df_select_descr = df[columns_sel_list]
    return df_select_descr

In [53]:
def descr_remover(df, descr_remove_list):
    columns_list = list(df.columns)
    columns_del_list = []
    for item in descr_remove_list:
        for del_item in columns_list:
            if re.search(item, del_item):
                columns_del_list.append(del_item)
    df_used_descr = df.drop(columns=columns_del_list, axis=1)
    return df_used_descr

In [54]:
def descr_enumerator(df, descr_enumerate_list):
    columns_list = list(df.columns)
    columns_enum_list = []
    for item in descr_enumerate_list:
        for sel_item in columns_list:
            if re.search(item, sel_item):
                columns_enum_list.append(sel_item)
    df_cat = df[columns_enum_list]
    print("No. of columns to enumerate: {}".format(len(df_cat.columns)))
    df_cat_oh = pd.get_dummies(df_cat)
    print("No. of columns after enumeration: {}".format(len(df_cat_oh.columns)))
    print("Columns enumerated: {}".format(df_cat_oh.columns))
    df.drop(labels=columns_enum_list, axis=1, inplace=True)
    df_num_oh = pd.concat([df, df_cat_oh], axis=1)
    return df_num_oh

In [55]:
path_preprocessing

[{'transfo': 'remove',
  'params': {'descriptorNames': ['metadata.*',
    '*dmean*',
    '*dvar*',
    '*.min',
    '*.max',
    '*cov',
    'tonal.thpcp',
    'lowlevel.spectral_energyband_high.*',
    'lowlevel.silence_rate*']}},
 {'transfo': 'enumerate',
  'params': {'descriptorNames': ['tonal.chords_key',
    'tonal.chords_scale',
    'tonal.key_key',
    'tonal.key_scale']}}]

In [56]:
list_remover = path_preprocessing[0]["params"]["descriptorNames"]
list_remover

['metadata.*',
 '*dmean*',
 '*dvar*',
 '*.min',
 '*.max',
 '*cov',
 'tonal.thpcp',
 'lowlevel.spectral_energyband_high.*',
 'lowlevel.silence_rate*']

In [57]:
list_remover_update = list_descr_handler(list_remover)

In [58]:
list_remover_update

['metadata_',
 'dmean',
 'dvar',
 '_min',
 '_max',
 'cov',
 'tonal_thpcp',
 'lowlevel_spectral_energyband_high_',
 'lowlevel_silence_rate']

In [59]:
def descr_handling(df, processing):
    if processing["transfo"] == "remove":
        remove_list = list_descr_handler(processing["params"]["descriptorNames"])
        df = descr_remover(df, remove_list)
        print("items removed related to: {}".format(remove_list))
    if processing["transfo"] == "enumerate":
        enumerate_list = list_descr_handler(processing["params"]["descriptorNames"])
        print("items enumerated related to:: {}".format(enumerate_list))
        df = descr_enumerator(df, enumerate_list)
    if processing["transfo"] == "select":
        select_list = list_descr_handler(processing["params"]["descriptorNames"])
        df = descr_selector(df, remove_list)
        print("items selected related to: {}".format(select_list))
    return df

In [60]:
df_clean = descr_handling(df_full_tracks, path_preprocessing[0])

items removed related to: ['metadata_', 'dmean', 'dvar', '_min', '_max', 'cov', 'tonal_thpcp', 'lowlevel_spectral_energyband_high_', 'lowlevel_silence_rate']


In [61]:
len(df_clean.columns)

680

In [62]:
df_enumerated = descr_handling(df_clean, path_preprocessing[1])

items enumerated related to:: ['tonal_chords_key', 'tonal_chords_scale', 'tonal_key_key', 'tonal_key_scale']
No. of columns to enumerate: 4
No. of columns after enumeration: 28
Columns enumerated: Index(['tonal_chords_key_A', 'tonal_chords_key_A#', 'tonal_chords_key_B',
       'tonal_chords_key_C', 'tonal_chords_key_C#', 'tonal_chords_key_D',
       'tonal_chords_key_D#', 'tonal_chords_key_E', 'tonal_chords_key_F',
       'tonal_chords_key_F#', 'tonal_chords_key_G', 'tonal_chords_key_G#',
       'tonal_chords_scale_major', 'tonal_chords_scale_minor',
       'tonal_key_key_A', 'tonal_key_key_A#', 'tonal_key_key_B',
       'tonal_key_key_C', 'tonal_key_key_C#', 'tonal_key_key_D',
       'tonal_key_key_D#', 'tonal_key_key_E', 'tonal_key_key_F',
       'tonal_key_key_F#', 'tonal_key_key_G', 'tonal_key_key_G#',
       'tonal_key_scale_major', 'tonal_key_scale_minor'],
      dtype='object')


In [63]:
len(df_enumerated.columns)

704

In [64]:
df_enumerated.head()

danceability  lowlevel_average_loudness  lowlevel_barkbands_crest_mean  \
0      danceable                   0.940232                      10.807129   
1  not_danceable                   0.918468                       8.789837   
2  not_danceable                   0.903639                       8.958855   
3      danceable                   0.964146                       7.989666   
4      danceable                   0.923212                       9.249996   

   lowlevel_barkbands_crest_median  lowlevel_barkbands_crest_var  \
0                         9.691339                     24.122204   
1                         8.108212                     12.385103   
2                         8.116771                     14.455623   
3                         7.193906                     11.031219   
4                         8.158960                     18.725180   

   lowlevel_barkbands_flatness_db_mean  lowlevel_barkbands_flatness_db_median  \
0                             0.176747                               0.146083   
1                             0.113029                               0.105044   
2                             0.126804                               0.123771   
3                             0.096527                               0.074531   
4                             0.115602                               0.095726   

   lowlevel_barkbands_flatness_db_var  lowlevel_barkbands_kurtosis_mean  \
0                            0.010974                          6.762696   
1                            0.001940                          2.929853   
2                            0.000906                          0.766920   
3                            0.006061                          2.024123   
4                            0.003345                          3.395818   

   lowlevel_barkbands_kurtosis_median  lowlevel_barkbands_kurtosis_var  \
0                            1.556325                       522.650879   
1                            0.664307                        45.587414   
2                           -0.279621                        13.023299   
3                            0.724629                        17.895559   
4                            0.216489                       102.163467   

   lowlevel_barkbands_skewness_mean  lowlevel_barkbands_skewness_median  \
0                          1.535155                            1.272417   
1                          1.394414                            1.197365   
2                          0.390109                            0.189988   
3                          1.261587                            1.155293   
4                          1.391440                            1.109180   

   lowlevel_barkbands_skewness_var  lowlevel_barkbands_spread_mean  \
0                         2.187619                       19.025879   
1                         1.433683                       27.515455   
2                         1.273380                       31.218849   
3                         0.704251                       29.787991   
4                         1.551799                       28.817030   

   lowlevel_barkbands_spread_median  lowlevel_barkbands_spread_var  \
0                         17.504620                     164.326553   
1                         26.352985                     159.659363   
2                         30.656132                     172.206955   
3                         29.554728                     162.274734   
4                         31.164455                     211.944901   

   lowlevel_dissonance_mean  lowlevel_dissonance_median  \
0                  0.437224                    0.460024   
1                  0.473310                    0.478164   
2                  0.483429                    0.487293   
3                  0.471935                    0.478796   
4                  0.470958                    0.481814   

   lowlevel_dissonance_var  lowlevel_dynamic_complexity  \
0                 0.005112          

In [65]:
def basic_processing(df, list_preprocessing):
    for item in list_preprocessing:
        df = descr_handling(df, item)
    return df

In [66]:
df_yeah = basic_processing(df_full_tracks, path_preprocessing)

items removed related to: ['metadata_', 'dmean', 'dvar', '_min', '_max', 'cov', 'tonal_thpcp', 'lowlevel_spectral_energyband_high_', 'lowlevel_silence_rate']
items enumerated related to:: ['tonal_chords_key', 'tonal_chords_scale', 'tonal_key_key', 'tonal_key_scale']
No. of columns to enumerate: 4
No. of columns after enumeration: 28
Columns enumerated: Index(['tonal_chords_key_A', 'tonal_chords_key_A#', 'tonal_chords_key_B',
       'tonal_chords_key_C', 'tonal_chords_key_C#', 'tonal_chords_key_D',
       'tonal_chords_key_D#', 'tonal_chords_key_E', 'tonal_chords_key_F',
       'tonal_chords_key_F#', 'tonal_chords_key_G', 'tonal_chords_key_G#',
       'tonal_chords_scale_major', 'tonal_chords_scale_minor',
       'tonal_key_key_A', 'tonal_key_key_A#', 'tonal_key_key_B',
       'tonal_key_key_C', 'tonal_key_key_C#', 'tonal_key_key_D',
       'tonal_key_key_D#', 'tonal_key_key_E', 'tonal_key_key_F',
       'tonal_key_key_F#', 'tonal_key_key_G', 'tonal_key_key_G#',
       'tonal_key_scale_

In [67]:
len(df_yeah.columns)

704

In [68]:
df_yeah.head()

danceability  lowlevel_average_loudness  lowlevel_barkbands_crest_mean  \
0      danceable                   0.940232                      10.807129   
1  not_danceable                   0.918468                       8.789837   
2  not_danceable                   0.903639                       8.958855   
3      danceable                   0.964146                       7.989666   
4      danceable                   0.923212                       9.249996   

   lowlevel_barkbands_crest_median  lowlevel_barkbands_crest_var  \
0                         9.691339                     24.122204   
1                         8.108212                     12.385103   
2                         8.116771                     14.455623   
3                         7.193906                     11.031219   
4                         8.158960                     18.725180   

   lowlevel_barkbands_flatness_db_mean  lowlevel_barkbands_flatness_db_median  \
0                             0.176747                               0.146083   
1                             0.113029                               0.105044   
2                             0.126804                               0.123771   
3                             0.096527                               0.074531   
4                             0.115602                               0.095726   

   lowlevel_barkbands_flatness_db_var  lowlevel_barkbands_kurtosis_mean  \
0                            0.010974                          6.762696   
1                            0.001940                          2.929853   
2                            0.000906                          0.766920   
3                            0.006061                          2.024123   
4                            0.003345                          3.395818   

   lowlevel_barkbands_kurtosis_median  lowlevel_barkbands_kurtosis_var  \
0                            1.556325                       522.650879   
1                            0.664307                        45.587414   
2                           -0.279621                        13.023299   
3                            0.724629                        17.895559   
4                            0.216489                       102.163467   

   lowlevel_barkbands_skewness_mean  lowlevel_barkbands_skewness_median  \
0                          1.535155                            1.272417   
1                          1.394414                            1.197365   
2                          0.390109                            0.189988   
3                          1.261587                            1.155293   
4                          1.391440                            1.109180   

   lowlevel_barkbands_skewness_var  lowlevel_barkbands_spread_mean  \
0                         2.187619                       19.025879   
1                         1.433683                       27.515455   
2                         1.273380                       31.218849   
3                         0.704251                       29.787991   
4                         1.551799                       28.817030   

   lowlevel_barkbands_spread_median  lowlevel_barkbands_spread_var  \
0                         17.504620                     164.326553   
1                         26.352985                     159.659363   
2                         30.656132                     172.206955   
3                         29.554728                     162.274734   
4                         31.164455                     211.944901   

   lowlevel_dissonance_mean  lowlevel_dissonance_median  \
0                  0.437224                    0.460024   
1                  0.473310                    0.478164   
2                  0.483429                    0.487293   
3                  0.471935                    0.478796   
4                  0.470958                    0.481814   

   lowlevel_dissonance_var  lowlevel_dynamic_complexity  \
0                 0.005112          

In [69]:
df_full_tracks.head()

danceability  lowlevel_average_loudness  lowlevel_barkbands_crest_dmean  \
0      danceable                   0.940232                        2.766660   
1  not_danceable                   0.918468                        2.675291   
2  not_danceable                   0.903639                        2.680212   
3      danceable                   0.964146                        2.334805   
4      danceable                   0.923212                        2.654776   

   lowlevel_barkbands_crest_dmean2  lowlevel_barkbands_crest_dvar  \
0                         4.448297                       5.745806   
1                         4.377324                       6.211648   
2                         4.377909                       5.717108   
3                         3.876004                       6.314280   
4                         4.302909                       6.634628   

   lowlevel_barkbands_crest_dvar2  lowlevel_barkbands_crest_max  \
0                       14.987641                     26.722847   
1                       15.621523                     26.676046   
2                       13.717224                     24.490746   
3                       16.660341                     24.082594   
4                       16.935333                     26.224245   

   lowlevel_barkbands_crest_mean  lowlevel_barkbands_crest_median  \
0                      10.807129                         9.691339   
1                       8.789837                         8.108212   
2                       8.958855                         8.116771   
3                       7.989666                         7.193906   
4                       9.249996                         8.158960   

   lowlevel_barkbands_crest_min  lowlevel_barkbands_crest_var  \
0                      2.798266                     24.122204   
1                      2.419000                     12.385103   
2                      2.538304                     14.455623   
3                      2.510511                     11.031219   
4                      2.489789                     18.725180   

   lowlevel_barkbands_flatness_db_dmean  \
0                              0.023720   
1                              0.021670   
2                              0.020029   
3                              0.017094   
4                              0.020814   

   lowlevel_barkbands_flatness_db_dmean2  lowlevel_barkbands_flatness_db_dvar  \
0                               0.035958                             0.000526   
1                               0.033876                             0.000391   
2                               0.032708                             0.000378   
3                               0.027388                             0.000365   
4                               0.032149                             0.000563   

   lowlevel_barkbands_flatness_db_dvar2  lowlevel_barkbands_flatness_db_max  \
0                              0.001158                            0.627938   
1                              0.000961                            0.448718   
2                              0.000948                            0.291119   
3                              0.000918                            0.561661   
4                              0.001232                            0.386401   

   lowlevel_barkbands_flatness_db_mean  lowlevel_barkbands_flatness_db_median  \
0                             0.176747                               0.146083   
1                             0.113029                               0.105044   
2                             0.126804                               0.123771   
3                             0.096527                               0.074531   
4                             0.115602                               0.095726   

   lowlevel_barkbands_flatness_db_min  lowlevel_barkbands_flatness_db_var  \
0                            0.040839                            0.010974   
1                            0.025457      

In [71]:
len(df_full_tracks.columns)

2675

In [72]:
len(df_yeah.columns)

704

# Post-processing

## Selecting the kind of learning and taking the corresponding features + Cleaning

In [73]:
# train kind: svm, deep_learning, supervised
train_kind = 'svm'

**X data**

In [86]:
X = df_tracks_ml.drop(labels=[class_name], axis=1)

In [87]:
X.shape

(225, 2675)

**y data**

In [88]:
y = df_tracks_ml[class_name]

In [89]:
X.head()

lowlevel_average_loudness  lowlevel_barkbands_crest_dmean  \
0                   0.940232                        2.766660   
1                   0.918468                        2.675291   
2                   0.903639                        2.680212   
3                   0.964146                        2.334805   
4                   0.923212                        2.654776   

   lowlevel_barkbands_crest_dmean2  lowlevel_barkbands_crest_dvar  \
0                         4.448297                       5.745806   
1                         4.377324                       6.211648   
2                         4.377909                       5.717108   
3                         3.876004                       6.314280   
4                         4.302909                       6.634628   

   lowlevel_barkbands_crest_dvar2  lowlevel_barkbands_crest_max  \
0                       14.987641                     26.722847   
1                       15.621523                     26.676046   
2                       13.717224                     24.490746   
3                       16.660341                     24.082594   
4                       16.935333                     26.224245   

   lowlevel_barkbands_crest_mean  lowlevel_barkbands_crest_median  \
0                      10.807129                         9.691339   
1                       8.789837                         8.108212   
2                       8.958855                         8.116771   
3                       7.989666                         7.193906   
4                       9.249996                         8.158960   

   lowlevel_barkbands_crest_min  lowlevel_barkbands_crest_var  \
0                      2.798266                     24.122204   
1                      2.419000                     12.385103   
2                      2.538304                     14.455623   
3                      2.510511                     11.031219   
4                      2.489789                     18.725180   

   lowlevel_barkbands_flatness_db_dmean  \
0                              0.023720   
1                              0.021670   
2                              0.020029   
3                              0.017094   
4                              0.020814   

   lowlevel_barkbands_flatness_db_dmean2  lowlevel_barkbands_flatness_db_dvar  \
0                               0.035958                             0.000526   
1                               0.033876                             0.000391   
2                               0.032708                             0.000378   
3                               0.027388                             0.000365   
4                               0.032149                             0.000563   

   lowlevel_barkbands_flatness_db_dvar2  lowlevel_barkbands_flatness_db_max  \
0                              0.001158                            0.627938   
1                              0.000961                            0.448718   
2                              0.000948                            0.291119   
3                              0.000918                            0.561661   
4                              0.001232                            0.386401   

   lowlevel_barkbands_flatness_db_mean  lowlevel_barkbands_flatness_db_median  \
0                             0.176747                               0.146083   
1                             0.113029                               0.105044   
2                             0.126804                               0.123771   
3                             0.096527                               0.074531   
4                             0.115602                               0.095726   

   lowlevel_barkbands_flatness_db_min  lowlevel_barkbands_flatness_db_var  \
0                            0.040839                            0.010974   
1                            0.025457                            0.001940   
2                            0.045240                  

In [90]:
# check the dtypes if are all OK
# X.dtypes

In [91]:
type(y)

pandas.core.series.Series

## Scaling

### Scaling the data

In [92]:
scaler = StandardScaler()

In [93]:
scaler.fit(X)

StandardScaler(copy=True, with_mean=True, with_std=True)

In [94]:
X_norm = scaler.transform(X)

In [95]:
X_norm

array([[ 0.6284611 , -0.30687451, -0.21902026, ..., -0.21566555,
        -1.11803399,  1.11803399],
       [ 0.54150004, -0.48057098, -0.30306602, ..., -0.21566555,
        -1.11803399,  1.11803399],
       [ 0.48225165, -0.47121687, -0.30237317, ..., -0.21566555,
         0.89442719, -0.89442719],
       ...,
       [-2.88465221, -0.35621679, -0.37293917, ..., -0.21566555,
         0.89442719, -0.89442719],
       [ 0.45241942, -0.56181505, -0.57801024, ..., -0.21566555,
        -1.11803399,  1.11803399],
       [-1.03276425, -0.61696614, -0.64636613, ..., -0.21566555,
        -1.11803399,  1.11803399]])

### Save the scaler model locally

In [96]:
# save the scaler
scaler_filename = 'scaler.pkl'
pickle.dump(scaler, open(scaler_filename, 'wb'))

### Load the scaler and test if it works fine on the same data

In [97]:
# load the scaler
scaler_new = pickle.load(open(scaler_filename, 'rb'))

In [98]:
X_norm_from_loaded_scaler = scaler_new.transform(X)

In [99]:
X_norm_from_loaded_scaler

array([[ 0.6284611 , -0.30687451, -0.21902026, ..., -0.21566555,
        -1.11803399,  1.11803399],
       [ 0.54150004, -0.48057098, -0.30306602, ..., -0.21566555,
        -1.11803399,  1.11803399],
       [ 0.48225165, -0.47121687, -0.30237317, ..., -0.21566555,
         0.89442719, -0.89442719],
       ...,
       [-2.88465221, -0.35621679, -0.37293917, ..., -0.21566555,
         0.89442719, -0.89442719],
       [ 0.45241942, -0.56181505, -0.57801024, ..., -0.21566555,
        -1.11803399,  1.11803399],
       [-1.03276425, -0.61696614, -0.64636613, ..., -0.21566555,
        -1.11803399,  1.11803399]])